In [1]:
import pandas as pd
import os
import json
import datetime

time_now = datetime.datetime.now().strftime("%Y-%m-%dT%H-%M-%S")

In [2]:
df = pd.read_csv("results.csv")
new_df = df.groupby(["model", "problem"], as_index=False)[['weighted_accuracy']].sum()

In [3]:
new_df.model.unique()

array(['Claude 2', 'Claude Instant', 'GPT 3.5 Turbo', 'GPT 4 Turbo',
       'MPT-30b', 'Mistral-7b', 'PaLM 2', 'Phi-1.5', 'Phi-2', 'Qwen-14b',
       'Vicuna-13b', 'Yi-34b'], dtype=object)

- https://grabon.com/blog/claude-users-statistics/
- https://medium.com/@seanbetts/peering-inside-gpt-4-understanding-its-mixture-of-experts-moe-architecture-2a42eb8bdcb3
- https://www.cnbc.com/2023/05/16/googles-palm-2-uses-nearly-five-times-more-text-data-than-predecessor.html

In [4]:
open_models = {
    "Yi-34b": "01-ai/Yi-34B-Chat",
    "Mistral-7b": "mistralai/Mistral-7B-Instruct-v0.1",
    "Vicuna-13b": "lmsys/vicuna-13b-v1.3",
    "Phi-1.5": "microsoft/phi-1_5",
    "MPT-30b": "mosaicml/mpt-30b-instruct",
    "Phi-2": "microsoft/phi-2",
    "Qwen-14b": "Qwen/Qwen-14B-Chat",
}

model_params = {
    'Yi-34b': ('torch.bfloat16', 34.389),
    'Mistral-7b': ('torch.bfloat16', 7.242),
    'Vicuna-13b': ('torch.float16', 13.0),
    'Phi-1.5': ('torch.float16', 1.3),
    'MPT-30b': ('torch.bfloat16', 30.0),
    'Phi-2': ('torch.float16', 2.78),
    'Qwen-14b': ('torch.bfloat16', 14.167),
    'Claude 2': ('?', 176),
    'Claude Instant': ('?', 60),
    "GPT 3.5 Turbo": ('?', 175),
    "GPT 4 Turbo": ('?', 1760),
    'PaLM 2': ('?', 340),
}

In [5]:
def result_export(model_df, model_name):
    model_df = model_df.set_index("problem")
    model_df = model_df.drop(columns=["model"])
    model_df = model_df.to_dict(orient="index")
    convert_problem_name = lambda x: x.replace("_Results", "").replace("Results", "").replace("bsp", "sas").upper()
    model_df = {convert_problem_name(k): v for k, v in model_df.items()}
    return model_df

In [6]:
for model in new_df.model.unique():   
    model_dir = open_models[model] if model in open_models else model.replace(" ", "-")
    # os.system(f"rm -rf {model_dir.split('/')[0]}")
    os.makedirs(f"{model_dir}", exist_ok=True)
    model_df = new_df[new_df["model"] == model]
    model_result = result_export(model_df, model)
    model_result = {
        "config": {
            "model_name": model_dir, 
            "model_type": "open-source" if model in open_models else "close-source",
            "model_dtype": model_params[model][0] if model in model_params else "?",
            "num_params": model_params[model][1] if model in model_params else 0,
        },
        "results": model_result
    }
    with open(f"{model_dir}/results_{time_now}.json", "w") as f:
        json.dump(model_result, f, indent=4)